In [5]:
%matplotlib tk
import time, math
from random import random
import numpy as np
from IPython import display
from PIL import Image
import matplotlib.pyplot as plt
import matplotlib.animation as animation
writer = animation.writers['ffmpeg'](fps=30, metadata=dict(artist='Me'), bitrate=1800)

# Коды элементов

BAD = 0
GOOD = 1
BASIC_FLOOR = 2
FENCE_PORT = 3
CORNER_PORT = 4
STORAGE_PORT = 5
GATE_LEAF_PORT = 6
GATE_PORT = 7
TRACK = 8
MACHINE_PORT = 9
WORK_PORT = 10
MM_PORT = 11
POWER_PORT = 12
UTIL_PORT = 13
PLANNER_PORT = 14
MINE_PORT = 15

#Словарь, где хранятся ссылки на клетки по координатам

cells={}

class FloorElement():
    def __init__(self,parent,x,y,element_type):
        self.x=x
        self.y=y
        self.element_type=element_type
        self.parent=parent
        self.parent.floor[(self.x,self.y)]=self

class Cell():
    def __init__(self,x,y):
        self.x=x
        self.y=y
        cells[(self.x,self.y)] = self
        self.floor={}
        self.content={}
        self.generate()
    def destroy(self):
        del cells[(self.x,self.y)] 
    def generate(self):

        # Настройка параметров клетки
        self.max_machine_size=20               # Максимальное число блоков в машине 
        self.work_machine_number_max=30         # Максимальное число рабочих машин
        self.planners_max=3                     # Максимальное число планировщиков
        self.utils_max=3                        # Максимальное число утилизаторов
        self.powers_max=4                       # Максимальное число электростанций
        self.mines_max=4                        # Максимальное число шахт
        self.storage_number_max_without_mm=500  # Максимальная емкость склада
        self.mm_max=50                          # Максимальное число мобильных манипуляторов (ММ)
        
        self.work_machine_number_rep=12         # Число рабочих машин, достаточное для репликации
        self.storage_number_rep_without_mm=200  # Емкость склада, достаточная для репликации
        self.work_machine_number_grow=6         # Число рабочих машин, достаточное для автономного роста
        self.storage_number_grow_without_mm=100 # Емкость склада, достаточная для автономного роста
        self.storage_free=15                    # Число складских ячеек в резерве
        self.machine_free=2                     # Число машиномест в резерве 

        # Найти общее количество машин (включая служебные) и общую емкость склада (включая места для ММ)
        
        self.machine_number_max=self.work_machine_number_max+self.planners_max+self.utils_max+self.powers_max+self.mines_max
        self.storage_number_max=self.mm_max+self.storage_number_max_without_mm

        # Подобрать прямоугольную форму машины, по возможности близкую к квадратной, содержащую количество
        # блоков не меньше заданного и хорошо стыкуемую с соседями, дорожками и складской зоной
        # Определить ширину и высоту машины, фактическое количество в ней блоков и занимаемую ей площадь
        
        self.machine_height=round(math.sqrt(self.max_machine_size),0)//3*3+1
        self.machine_width=self.max_machine_size//self.machine_height
        if self.machine_width*self.machine_height<self.max_machine_size:
            self.machine_width=self.machine_width+1
        self.fact_machine_size=self.machine_height*self.machine_width
        self.fact_machine_area=(self.machine_height+5)*(self.machine_width+5)

        # Подобрать прямоугольную форму рабочей зоны, по возможности близкую к квадратной, содержащую 
        # количество машин не меньше заданного и хорошо стыкуемую с дорожками и складскими зонами
        # Определить ширину и высоту рабочей зоны, фактическое количество машин и занимаемую ей площадь
        
        self.machine_coloumns=round(math.sqrt(self.machine_number_max),0)
        self.machine_rows=self.machine_coloumns
        if self.machine_coloumns*self.machine_rows<self.machine_number_max:
            self.machine_rows+=1
        if self.machine_width%2==0:
            if self.machine_coloumns%2==1:
                if self.machine_coloumns%2==1:
                    self.machine_coloumns+=1
                else:
                    self.machine_coloumns,self.machine_rows=self.machine_rows,self.machine_coloumns
        self.siderows=self.machine_rows*(1+(self.machine_height-1)/6)
        if self.siderows!=int(self.siderows):
            self.machine_rows+=1
        self.siderows=self.machine_rows*(1+(self.machine_height-1)/6) 
        self.fact_machine_number=self.machine_coloumns*self.machine_rows

        # Рассчитать размер территории, занимаемой клеткой
        
        self.fact_machine_block_area=self.fact_machine_number*self.fact_machine_area
        self.storage_desired_area=self.storage_number_max*5.5
        self.total_desired_area=self.storage_desired_area+self.fact_machine_block_area
        self.presize=(int(math.sqrt(self.total_desired_area)))
        self.presize=(1+self.presize//6)*6
        if (self.presize-(self.siderows*6))%12!=0:
            self.presize+=6
        self.realsize=self.presize+5

        # Создать территорию
        
        self.Terrain=np.ones((self.realsize,self.realsize))
        #Terrain=np.sign(np.array(Image.open("intest.png"))[:,:,0])

        # Создать карту, заполненную элементами пола
        
        self.Map=self.Terrain*BASIC_FLOOR

        # Создать забор
        
        self.Map[0]=self.Map[-1]=self.Map[:,0]=self.Map[:,-1]=FENCE_PORT

        # Создать углы
        
        self.Map[0,0]=self.Map[0,-1]=self.Map[-1,0]=self.Map[-1,-1]=CORNER_PORT

        # Создать трассу по периметру клетки
        
        self.Map[2:-2,2:-2]=TRACK
        self.Map[3:-3,3:-3]=BASIC_FLOOR

        # Создать ворота, порты ворот, складские места
        
        for y in range(4,self.presize+2,6):
            self.Map[y-2,2:-3]=TRACK
            self.Map[y,0]=self.Map[y+2,0]=self.Map[y,-1]=self.Map[y+2,-1]=GATE_LEAF_PORT
            self.Map[0,y]=self.Map[0,y+2]=self.Map[-1,y]=self.Map[-1,y+2]=GATE_LEAF_PORT
            self.Map[y+1,0]=self.Map[y+1,-1]=self.Map[0,y+1]=self.Map[-1,y+1]=GATE_PORT
            self.Map[y+1,1]=self.Map[y+1,-2]=self.Map[1,y+1]=self.Map[-2,y+1]=TRACK
            for x in range(4,self.presize+2,2):
                self.Map[y,x]=self.Map[y+2,x]=STORAGE_PORT
                
        # Создать машинную зону   
        
        self.center=int(self.realsize/2)
        self.mxstart=int(self.center-(self.machine_coloumns*(self.machine_width+5))/2)
        self.mystart=int(self.center-(self.siderows*3))
        self.mxstop=int(self.center+(self.machine_coloumns*(self.machine_width+5))/2)
        if self.mxstart%2!=0:
            self.mxstart-=1
            self.mxstop-=1
        self.mystop=int(self.center+(self.siderows*3))
        
        self.Map[self.mystart+1:self.mystop-1,self.mxstart:self.mxstop]=BASIC_FLOOR
        self.Map[2:-2,self.mxstart]=self.Map[2:-2,self.mxstop]=TRACK

        special_machines_list=([PLANNER_PORT]*self.planners_max+[POWER_PORT]*self.powers_max+
            [UTIL_PORT]*self.utils_max+[MINE_PORT]*self.mines_max)
        
        for y in range(self.mystart,self.mystop,int(self.machine_height)+5):
            self.Map[y,self.mxstart:self.mxstop]=TRACK
            for x in range(self.mxstart,self.mxstop,int(self.machine_width)+5):
                kind=MACHINE_PORT
                if len(special_machines_list)>0:
                    kind = special_machines_list.pop(0)
                self.Map[3+y:3+y+int(self.machine_height),3+x:3+x+int(self.machine_width)]=kind
                for sy in range(3+y,3+y+int(self.machine_height),2):
                    self.Map[sy,2+x]=WORK_PORT
                for sx in range(4+x,3+x+int(self.machine_width),2):
                    self.Map[2+y,sx]=WORK_PORT
                zystart=3+y
                if self.Map[2+y,2+x+int(self.machine_width)]==WORK_PORT:
                    zystart+=1
                for zy in range(zystart,3+y+int(self.machine_height),2):
                    self.Map[zy,3+x+int(self.machine_width)]=WORK_PORT
                zxstart=3+x
                if self.Map[2+y+int(self.machine_height),2+x]==WORK_PORT:
                    zxstart+=1
                for zx in range(zxstart,3+x+int(self.machine_width),2):
                    self.Map[3+y+int(self.machine_height),zx]=WORK_PORT

        # Создать дополнительные вертикальные трассы возле машинной зоны   
        
        for x in range(self.mxstart,self.mxstop,int(self.machine_width)+5):
            if self.Map[4,x] == STORAGE_PORT:
                self.Map[2:-3,x]=TRACK
            else:
                self.Map[self.mystart:self.mystop,x]=TRACK

        # Создать порты мобильных манипуляторов
        
        mm_counter=self.mm_max
        for y in range(self.realsize):
            for x in range(self.realsize):
                if mm_counter>0:
                    if self.Map[y,x]==STORAGE_PORT:
                        self.Map[y,x]=MM_PORT
                        mm_counter-=1
                        if self.Map[y-2,x]==TRACK:
                            self.Map[y-1,x]=TRACK
                        elif self.Map[y+2,x]==TRACK:
                            self.Map[y+1,x]=TRACK

        # Зарегистрировать элементы карты
        
        for y in range(self.realsize):
            for x in range(self.realsize):
                if self.Map[y,x]>1:                          
                    FloorElement(self,x,y,self.Map[y,x])
                                                     
# Создать клетку                            
                            
c=Cell(20,20)

# Показать клетку

fig=plt.figure(figsize=(7, 5))
ax=fig.add_subplot(1, 1, 1)
im1=plt.imshow(c.Map, cmap=plt.get_cmap('bone'))
ax.set_title('Map MS:'+str(c.max_machine_size)+' MN:'+str(c.work_machine_number_max)+
             ' SN:'+str(c.storage_number_max_without_mm)+' MM:'+str(c.mm_max))          
plt.show()